## Search for SLC Sentinel-1 products

In [1]:
import lxml.etree as etree
import requests
import cioppy
ciop = cioppy.Cioppy()

In [2]:
def get_params(osd):

    oss_ns = {'a':'http://www.w3.org/2001/XMLSchema', 
          'b':'http://www.w3.org/2001/XMLSchema-instance',
          'c':'http://a9.com/-/opensearch/extensions/time/1.0/',
          'd':'http://www.opengis.net/eop/2.0',
          'e':'http://purl.org/dc/terms/',
          'f':'http://a9.com/-/spec/opensearch/extensions/parameters/1.0/',
          'g':'http://purl.org/dc/elements/1.1/',
          'h':'http://www.terradue.com/opensearch',
          'i':'http://a9.com/-/opensearch/extensions/geo/1.0/',
          'j':'http://a9.com/-/spec/opensearch/1.1/'}
    
    oss_content = etree.fromstring(requests.get(osd).content)
    
    url_template_element = oss_content.xpath('/j:OpenSearchDescription/j:Url[@type="application/atom+xml"]',
                                                 namespaces=oss_ns)[0]
    
    parameters = dict()
    
    for index, parameter in enumerate(url_template_element.xpath('.//f:Parameter', namespaces=oss_ns)):
        
        parameters[parameter.attrib['name']] = {'title' : parameter.attrib['title'], 
                                                'value' : parameter.attrib['value']}
        
        options = []
        for option in parameter.xpath('.//f:Option', namespaces=oss_ns):
            
            options.append(option.attrib['value'])
    
        parameters[parameter.attrib['name']] = {'title' : parameter.attrib['title'], 
                                                'value' : parameter.attrib['value'],
                                                'options' : options}
    return parameters

In [3]:
def get_param_value(osd, os_parameter):

    params = get_params(osd)

    res = None
    
    for index, param in enumerate(params):
        
        if params[param]['value'] == os_parameter:
            
            res = params[param]
            res['name'] = param
     
    return res

Define the Sentinel-1 endpoint

In [4]:
s1_osd_url = 'https://catalog.terradue.com/sentinel1/description'

Get the Sentinel-1 search parameters

In [5]:
s1_parameters = get_params(s1_osd_url)

Print all the OpenSearch parameters

In [6]:
for key, value in s1_parameters.iteritems():

    print '%24s' % s1_parameters[key]['value'], s1_parameters[key]['title'] 

              {geo:uid?} The identifier of the resource within the search engine context (local reference)
    {t2:downloadOrigin?} a string that identifies the download origin (keyword, hostname...) to adapt the enclosure. If the parameter is enclosed between [] (e.g. [terradue]), enclosure will be returned only if there is a enclosure found for this source.
       {eop:cloudCover?} A number, set or interval requesting the cloud coverage
            {startIndex} index of the first search result desired
   {t2:vendorSpecifics?} A number, set or interval filtering vendor specific name:value
             {startPage} page number of the set of search results desired
       {eop:sensorType?} A string identifying the sensor type
     {eop:accessedFrom?} A string identifying the location from which the resource will be accessed. The catalogue shall return the download location in the enclosure atom link according to the parameter value.
         {t2:landCover?} A number, set or interval reque

# Find the parameter associated to **'{eop:productType?}'** and its options

In [7]:
product_type_parameter = get_param_value(s1_osd_url, '{eop:productType?}')
download_origin_parameter = get_param_value(s1_osd_url, '{t2:downloadOrigin?}')

In [8]:
product_type_parameter['name']

'pt'

In [9]:
options = s1_parameters[product_type_parameter['name']]['options']

In [10]:
options

['GRD', 'RAW', 'SLC', 'OCN']

Now search for SLC products creating a dictionary with the search parameters

In [11]:
search_params = dict([(product_type_parameter['name'], 
                       options[2]),(download_origin_parameter['name'], 'terradue')])

In [12]:
search_params

{'do': 'terradue', 'pt': 'SLC'}

In [13]:
sensor_type_parameter = get_param_value(s1_osd_url, '{eop:sensorType?}')

In [14]:
sensor_type_parameter['name']

'st'

In [15]:
options = s1_parameters[sensor_type_parameter['name']]['options']

In [16]:
search = ciop.search(end_point=s1_osd_url,
                     params=search_params,
                     output_fields='self,productType,track,enclosure,identifier,wkt,startdate,enddate,polarisationChannels', 
                     model='EOP')

Show the first result returned

In [17]:
search[0]

{'enclosure': 'https://store.terradue.com/download/sentinel1/files/v1/S1B_WV_SLC__1SSV_20190507T080616_20190507T081452_016135_01E5BC_48A6',
 'enddate': '2019-05-07T08:14:52.3990000Z',
 'identifier': 'S1B_WV_SLC__1SSV_20190507T080616_20190507T081452_016135_01E5BC_48A6',
 'polarisationChannels': 'VV',
 'productType': 'SLC',
 'self': 'https://catalog.terradue.com/sentinel1/search?format=atom&uid=S1B_WV_SLC__1SSV_20190507T080616_20190507T081452_016135_01E5BC_48A6',
 'startdate': '2019-05-07T08:06:16.8280000Z',
 'track': '9',
 'wkt': 'POLYGON((-53.356213 -55.926842,-53.234772 -55.763161,-50.32679 -55.642445,-49.999165 -55.711193,-49.890366 -55.539688,-48.947655 -54.019253,-47.956585 -52.322357,-47.048164 -50.615124,-46.197945 -48.901337,-45.399315 -47.182137,-44.646126 -45.458092,-43.919273 -43.732742,-43.243015 -42.000259,-42.598835 -40.263813,-41.983528 -38.5242,-41.381111 -36.783916,-40.815392 -35.038166,-40.270462 -33.289383,-39.744553 -31.537874,-39.693222 -31.359335,-39.235916 -29.784

You can, of course, set the search parameters directly with:

In [18]:
search = ciop.search(end_point=s1_osd_url,
                     params={'pt': 'SLC'},
                     output_fields='self,productType,track,enclosure,identifier,wkt,startdate', 
                     model='EOP')

In [19]:
search[0]

{'enclosure': "https://scihub.copernicus.eu/apihub/odata/v1/Products('7245f5c4-eecd-4afb-9834-82bb021d96e1')/$value",
 'identifier': 'S1B_WV_SLC__1SSV_20190507T080616_20190507T081452_016135_01E5BC_48A6',
 'productType': 'SLC',
 'self': 'https://catalog.terradue.com/sentinel1/search?format=atom&uid=S1B_WV_SLC__1SSV_20190507T080616_20190507T081452_016135_01E5BC_48A6',
 'startdate': '2019-05-07T08:06:16.8280000Z',
 'track': '9',
 'wkt': 'POLYGON((-53.356213 -55.926842,-53.234772 -55.763161,-50.32679 -55.642445,-49.999165 -55.711193,-49.890366 -55.539688,-48.947655 -54.019253,-47.956585 -52.322357,-47.048164 -50.615124,-46.197945 -48.901337,-45.399315 -47.182137,-44.646126 -45.458092,-43.919273 -43.732742,-43.243015 -42.000259,-42.598835 -40.263813,-41.983528 -38.5242,-41.381111 -36.783916,-40.815392 -35.038166,-40.270462 -33.289383,-39.744553 -31.537874,-39.693222 -31.359335,-39.235916 -29.784475,-38.732239 -28.031361,-38.253826 -26.274025,-38.206898 -26.094782,-38.413788 -26.048946,-40.4